# Titanic: Machine Learning from Disaster

## Description

The sinking of the RMS Titanic is one of the most infamous shipwrecks in history.  On April 15, 1912, during her maiden voyage, the Titanic sank after colliding with an iceberg, killing 1502 out of 2224 passengers and crew. This sensational tragedy shocked the international community and led to better safety regulations for ships.

## Objective

Predict what sorts of people were likely to survive.

Inspiration:
   - https://www.kaggle.com/omarelgabry/titanic/a-journey-through-titanic
   - https://www.kaggle.com/poonaml/titanic/titanic-survival-prediction-end-to-end-ml-pipeline
   - https://www.kaggle.com/helgejo/titanic/an-interactive-data-science-tutorial
   - https://www.kaggle.com/arthurlu/titanic/exploratory-tutorial-titanic

## Table of contents


- [Description of the data set](#Description-of-the-data-set)
- [First look at the data](#First-look-at-the-data)
    - [Import Libraries](#Import-Libraries)
    - [Load Data](#Load-Data)
    - [Brief summaries](#Brief-summaries)
- [Visualization](#Visualization)
    - [Basic insight of the data](#Basic-insight-of-the-data)
    - [Focus on the mean of survival](#Focus-on-the-mean-of-survival)
- [Missing Values](#Missing-Values)
    - [Embarked](#Embarked)
    - [Fare](#Fare)
    - [Age with Median](#Age-with-median)
- [Features engineering](#Features-engineering)
    - [Name](#Name)
    - [Family](#Family)
    - [Name](#Name)
- [Visualization new Features](#Visualization-new-features)
    - [Visualization Name](#Visualization-Name)
    - [Visualization Family](#Visualization-Family)
- [Features Encoding](#Features-Encoding)
    - [Categorial features encoding](#Categorial features encoding)
        - [Label Encoding](#Label-Encoding)
        - [One Hot Encoding](#One-Hot-Encodingn)   
    - [Feature Scalling](#Feature-Scalling)
    - [Data Preparation](#Data-Preparation)
- [Features Importance](#Features-Importance)
    - [Correlation - Numerical label](#Correlation---Numerical-label)
    - [Correlation - One Hot Encoder](#Correlation---One-Hot-Encoder)
    - [LDA](#LDA)
    - [Select K Best](#Select-K-Best)
- [Model Selection](#Model-Selection)
    - [Helper function](#Helper-function)
    - [Gradient Boosting Classifier](#Gradient-Boosting-Classifier)
    - [Random Forest Classifier](#Random-Forest-Classifier)
    - [Adaboost](#Adaboost)
    - [SVC](#SVC)
    - [Logistic Regression](#Logistic-Regression)
    - [Voting Classifier](#Voting-Classifier)
- [Submission](#Submission)



- [Feature Selection](#Feature-selection)
- [Feature Selection](#Feature-selection)

### Description of the data set

## First look at the data

[[back to top](#Table-of-contents)]

### Import Libraries

In [ ]:
# Dataframe
import pandas as pd

# Visualization
from IPython.display import display, HTML
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from pprint import pprint
sns.set_style('whitegrid')
%matplotlib inline

# Sklearn
import sklearn as sk
# Pipeline
from sklearn.pipeline import Pipeline
# Preprocessing
from sklearn import preprocessing
from sklearn.preprocessing import LabelEncoder,StandardScaler
# Features and model selection
from sklearn.cross_validation import KFold
from sklearn.model_selection import train_test_split,GridSearchCV
from sklearn.feature_selection import SelectKBest, f_classif
# Metric
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
# Classifier
from sklearn.linear_model import LogisticRegression
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB,MultinomialNB
from sklearn.svm import SVC
from sklearn.ensemble import (ExtraTreesClassifier, RandomForestClassifier, 
                              AdaBoostClassifier, GradientBoostingClassifier, VotingClassifier)

from sklearn.metrics import f1_score,accuracy_score

# Warning
import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning) 
warnings.filterwarnings("ignore", category=RuntimeWarning)

### Load data

In [ ]:
# Load data directly into a dataframe
df_train=pd.read_csv("Data/Titanic/train.csv")
df_test=pd.read_csv("Data/Titanic/test.csv")

# Get a look at the first rows
df_train.head()

In [ ]:
df_test.head()

Variable Description
    - Survived: Survived (1) or died (0)
    - Pclass: Passenger's class
    - Name: Passenger's name
    - Sex: Passenger's sex
    - Age: Passenger's age
    - SibSp: Number of siblings/spouses aboard
    - Parch: Number of parents/children aboard
    - Ticket: Ticket number
    - Fare: Fare
    - Cabin: Cabin
    - Embarked: Port of embarkation
    
    Source of information : https://www.kaggle.com/c/titanic/data

### Brief summaries

In [ ]:
print("----------------------------------Informations for the training set----------------------------------\n")
df_train.info()
print('\n',df_train.isnull().sum())
print("\n----------------------------------Informations for the testing set ----------------------------------\n")
df_test.info()
print('\n',df_test.isnull().sum())

Note that:
    - No Survived feature on the testing set
    - Cabin feature is mostly null --> Will be dropped
    - Embarked feature has a few missing values
    - Some Ages are missing --> Will need to be completed or drop the missing rows
    - Survived and Pclass should be treated as object because they are qualitative

In [ ]:
# Dropping Cabin, Ticket and PassengerId
df_train=df_train.drop(['Cabin','PassengerId','Ticket'], axis=1)

df_test=df_test.drop(['Cabin','Ticket'], axis=1)
PassengerId = df_test['PassengerId']

In [ ]:
# Changing the type of Pclass and Survived 
df_train['Pclass']=df_train['Pclass'].astype(object)
df_train['Survived']=df_train['Survived'].astype(object)

df_test['Pclass']=df_test['Pclass'].astype(object)

In [ ]:
# Basic statistical information about quantitative and qualitative columns

print("----------------------------------Informations for the training set----------------------------------\n")
# Quantitative
display(df_train.describe())
# Qualitative
display(df_train.describe(include=['object']))
print("----------------------------------Informations for the testing set----------------------------------\n")
# Quantitative
display(df_test.describe())
# Qualitative
display(df_test.describe(include=['object']))

###  Visualization

[[back to top](#Table-of-contents)]

#### Basic insight of the data

In [ ]:
# Qualitative Data : [Survived, Sex, Embarked, Pclass] 
fig, (axis1,axis2,axis3,axis4) = plt.subplots(1,4,figsize=(15,5))
sns.countplot(x='Survived', data=df_train, ax=axis1)
sns.countplot(x='Sex', data=df_train, ax=axis2)
sns.countplot(x='Embarked', data=df_train, ax=axis3)
sns.countplot(x='Pclass', data=df_train, ax=axis4)
fig.suptitle("Basic representation of Qualitative data with count")

In [ ]:
# Discrete Quantitative Data : [SibSp, Parch] 
fig2, (axis1,axis2) = plt.subplots(1,2,figsize=(15,5))
sns.countplot(df_train['SibSp'],ax=axis1)
sns.countplot(df_train['Parch'],ax=axis2)
fig2.suptitle("Basic representation of Discrete Quantitative data with count")

In [ ]:
# Continuous Quantitative Data : [Age, Fare]
fig3, (axis1,axis2) = plt.subplots(2,1,figsize=(15,10))
sns.distplot(df_train['Age'].dropna(), bins=80, ax=axis1)
sns.distplot(df_train['Fare'], ax=axis2)
fig3.suptitle("Basic representation of Continuous Quantitative data with probability")

In [ ]:
# Age distribution within Sex and Pclass
fig3, ((axis1),(axis2),(axis3)) = plt.subplots(3,1,figsize=(15,15))

# Age distribution
df_train.Age.plot(kind='kde',ax=axis1)
axis1.set_xlabel("Age")    
axis1.set_title("Age Distribution")

# Age distribution within Sex
df_train.Age[df_train.Sex == 'male'].plot(kind='kde',ax=axis2,)    
df_train.Age[df_train.Sex == 'female'].plot(kind='kde',ax=axis2)
axis2.set_xlabel("Age")    
axis2.set_title("Age Distribution within Sex")
axis2.legend(('Male', 'Female'))

# Age distribution within Pclass
df_train.Age[df_train.Pclass == 1].plot(kind='kde',ax=axis3)    
df_train.Age[df_train.Pclass == 2].plot(kind='kde',ax=axis3)
df_train.Age[df_train.Pclass == 3].plot(kind='kde',ax=axis3)
axis3.set_xlabel("Age")    
axis3.set_title("Age Distribution within Classes")
axis3.legend(('1st Class', '2nd Class','3rd Class'))

#### Focus on the mean of survival

In [ ]:
# [Sex, Pclass, Embarked] by mean of survival
fig4, (axis1,axis2,axis3) = plt.subplots(1,3,figsize=(15,5))
sns.barplot(x='Sex',y='Survived', data=df_train, ax=axis1)
sns.barplot(x='Embarked',y='Survived', data=df_train, ax=axis2)
sns.barplot(x='Pclass',y='Survived', data=df_train, ax=axis3)
fig4.suptitle("Representation of features linked to the target : Survived ")

In [ ]:
# [SibSp, Parch] by mean of survival
fig6, (axis1,axis2) = plt.subplots(1,2,figsize=(15,5))
sns.barplot(x='SibSp',y='Survived', data=df_train, ax=axis1)
sns.barplot(x='Parch',y='Survived', data=df_train, ax=axis2)
fig6.suptitle("Representation of features linked to the target : Survived ")

In [ ]:
# Cross relation betwen [Sex, Pclass, Embarked] by mean of survival
fig5, ((axis1,axis2),(axis3,axis4),(axis5,axis6)) = plt.subplots(3,2,figsize=(15,15))
sns.barplot(x='Sex',y='Survived',hue='Pclass', data=df_train, ax=axis1)
sns.barplot(x='Sex',y='Survived',hue='Embarked', data=df_train, ax=axis2)

sns.barplot(x='Pclass',y='Survived',hue='Sex', data=df_train, ax=axis3)
sns.barplot(x='Pclass',y='Survived',hue='Embarked', data=df_train, ax=axis4)

sns.barplot(x='Embarked',y='Survived',hue='Sex', data=df_train, ax=axis5)
sns.barplot(x='Embarked',y='Survived',hue='Pclass', data=df_train, ax=axis6)

fig5.suptitle("Cross Representation of the features linked to the target : Survived")

In [ ]:
# Age by mean of survival
fig=sns.barplot(x='Age', y='Survived', data=df_train)

In [ ]:
# Age

# Kernel density of survivor and non survivor by Age
g1 = sns.FacetGrid( df_train , hue='Survived' , aspect=4)
g1.map( sns.kdeplot , 'Age' , shade= True )
g1.add_legend()

# Kernel density of survivor and non survivor by Age and Sex 
g2 = sns.FacetGrid( df_train , hue='Survived' , aspect=4 , row = 'Sex')
g2.map( sns.kdeplot , 'Age' , shade= True )
g2.add_legend()

# Kernel density of survivor and non survivor by Age and Pclass
g3 = sns.FacetGrid( df_train , hue='Survived' , aspect=4 , row = 'Pclass')
g3.map( sns.kdeplot , 'Age' , shade= True )
g3.add_legend()

In [ ]:
# Fare

# Scatterplot Fare & Age
g = sns.FacetGrid(df_train, hue="Survived", size=6)
g=g.map(plt.scatter, "Fare", "Age",edgecolor="w").add_legend()
g.add_legend()
g.set(xlim=(0, 550))

# Scatterplot Fare & Age by Sex
g = sns.FacetGrid(df_train, hue="Survived", col="Sex", margin_titles=True,
                palette="Set1",hue_kws=dict(marker=["^", "v"]),size=6)
g=g.map(plt.scatter, "Fare", "Age",edgecolor="w").add_legend()
g.add_legend()
g.set(xlim=(0, 300))

# Scatterplot Fare & Age by Pclass
g = sns.FacetGrid(df_train, col="Pclass", hue="Survived", size=4)
g=g.map(plt.scatter, "Fare", "Age",edgecolor="w").add_legend()
g.add_legend()
g.set(xlim=(0, 300))

# Scatterplot Fare & Age by Pclass & Sex
g = sns.FacetGrid(df_train, hue="Survived", col="Pclass", row="Sex" ,margin_titles=True,
                  palette={1:"red", 0:"grey"},size=5)
g=g.map(plt.scatter, "Fare", "Age",edgecolor="w").add_legend()
g.set(xlim=(0, 300))


### Features engineering

[[back to top](#Table-of-contents)]

#### Combined DataFrame

In [ ]:
# Creation of a dataframe with train and test for Feature Engineering
def get_combined_data():
    # reading train data
    train = pd.read_csv("Data/Titanic/train.csv")
    
    # reading test data
    test = pd.read_csv("Data/Titanic/test.csv")

    # extracting and then removing the targets from the training data 
    targets = train.Survived
    #train.drop('Survived',axis=1,inplace=True)

    # merging train data and test data for future feature engineering
    combined = train.append(test)
    combined.reset_index(inplace=True)
    combined.drop('index',axis=1,inplace=True)
    
    return combined

def recover_train_test_target(combined):
    
    train0 = pd.read_csv("Data/Titanic/train.csv")
    
    targets = train0.Survived
    train = combined.ix[0:890]
    test = combined.ix[891:]
    
    return train,test,targets

In [ ]:
combined = get_combined_data()

#### Name

In [ ]:
# Name

#Create feature for the length of name 
combined["Name_Length"] = combined["Name"].apply(lambda x: len(x))

# Create a categorical feature Name_Size
combined['Name_Size']=pd.cut(combined['Name_Length']
                            ,bins=[0,20,40,60,90]
                            ,labels=["Short","Medium","Long","Very Long"])

# Extract the title from each name
combined['Title'] = combined['Name'].map(lambda name:name.split(',')[1].split('.')[0].strip())

# Map for aggregated titles
Title_Dictionary = {
                    "Mme":        "Mrs",
                    "Mlle":       "Miss",
                    "Ms":         "Mrs",
                    "Mr" :        "Mr",
                    "Mrs" :       "Mrs",
                    "Miss" :      "Miss",
                    "Capt":       "Officer",
                    "Col":        "Officer",
                    "Major":      "Officer",
                    "Dr":         "Officer",
                    "Rev":        "Officer",
                    "Master" :    "Master",
                    "Lady" :      "Royalty",
                    "Jonkheer":   "Royalty",
                    "Don":        "Royalty",
                    "Sir" :       "Royalty",
                    "Dona":       "Royalty",
                    "the Countess":"Royalty"
                    }
    
# Mapping
combined['Title_aggr'] = combined.Title.map(Title_Dictionary)

#### Family

In [ ]:
# Family

# Creation of a feature Number_of_relatives = SibSp + Parch
combined['Number_of_relatives']=combined['SibSp']+combined['Parch']

# Creation of a categorical feature Size_Family
combined.loc[combined['Number_of_relatives'] == 0, 'Size_Family'] = 'Alone'
combined.loc[ (combined['Number_of_relatives'] > 0) 
            & (combined['Number_of_relatives'] < 4), 'Size_Family'] = 'Small'
combined.loc[combined['Number_of_relatives'] > 3, 'Size_Family'] = 'Big'

We can create 3 categories : 
    - Alone = 0
    - Small = [1,2,3]
    - Big = > 3

#### Cabin

In [ ]:
combined.shape

In [ ]:
# Mostly NaN values
combined.Cabin.isnull().sum()

In [ ]:
# Create a category Unknown
combined['Cabin'] = combined.Cabin.fillna( 'U' )

In [ ]:
# Get the first letter
combined["Deck"]=combined.Cabin.str[0]
Sort_Deck=combined.groupby('Deck').size()
Sort_Deck.sort_values(ascending=False,inplace=True)
display(Sort_Deck)

In [ ]:
sns.barplot(x='Deck', y='Survived', data=combined)

In [ ]:
# Creation of 4 categories
Deck_Dictionary = {
                    "E":        "C1",
                    "D":       "C1",
                    "B":         "C1",
                    "C" :        "C2",
                    "F" :       "C2",
                    "G" :      "C3",
                    "A":       "C3",
                    "U":        "U",
                    "T":        "U"
                    }

# Mapping
combined['Deck_aggr'] = combined.Deck.map(Deck_Dictionary)

sns.barplot(x='Deck_aggr', y='Survived', data=combined)

#### Ticket

In [ ]:
combined.Ticket.isnull().sum()

In [ ]:
Sort_Ticket=combined.groupby('Ticket').size()
Sort_Ticket.sort_values(ascending=False,inplace=True)
display(Sort_Ticket)

In [ ]:
# a function that extracts each prefix of the ticket, returns 'XXX' if no prefix (i.e the ticket is a digit)
def cleanTicket( ticket ):
    ticket = ticket.replace( '.' , '' )
    ticket = ticket.replace( '/' , '' )
    ticket = ticket.split()
    ticket = map( lambda t : t.strip() , ticket )
    ticket = list(filter( lambda t : not t.isdigit() , ticket ))
    if len( ticket ) > 0:
        return ticket[0]
    else: 
        return 'XXX'

In [ ]:
combined[ 'Ticket_clean' ] = combined[ 'Ticket' ].map( cleanTicket )

Sort_Clean_Ticket=combined.groupby('Ticket_clean').size()
Sort_Clean_Ticket.sort_values(ascending=False,inplace=True)
display(Sort_Clean_Ticket)

In [ ]:
g = plt.figure(figsize=(20,10)) 
g = sns.barplot(x='Ticket_clean',data=combined, y='Survived',order=['XXX','PC','CA','A5','SOTONOQ','WC','SCPARIS','STONO','A4','FCC','C','SOC','SOPP','STONO2','SCParis','SCAH','PP','LINE','WEP','FC','SOTONO2','PPP','SC','SWPP','SCA4','AS','AQ4','AQ3','SCA3','CASOTON','Fa','LP','SCOW','SOP','SP','STONOQ','A'])

In [ ]:
Ticket_Dictionary = {
                    "XXX":        "T1",
                    "PC":      "T2",
                    "CA":         "T3",
                    "A5" :        "T4",
                    "SOTONOQ" :       "T4",
                    "WC" :      "T4",
                    "SCPARIS":       "T5",
                    "STONO":        "T5",
                    "A4":        "T1",
                    "FCC":       "T1",
                    "C":         "T1",
                    "SOC" :        "T1",
                    "SOPP" :       "T1",
                    "STONO2" :      "T1",
                    "SCParis":       "T1",
                    "SCAH":     "T1",
                    "PP":        "T1",
                    "LINE":        "T1",
                    "WEP":       "T1",
                    "FC":         "T1",
                    "SOTONO2" :        "T1",
                    "PPP" :       "T1",
                    "SC" :      "T1",
                    "SWPP":       "T1",
                    "SCA4":        "T1",
                    "AS":        "T1",
                    "AQ4":        "T1",
                    "AQ3":       "T1",
                    "SCA3":         "T1",
                    "CASOTON" :        "T1",
                    "Fa" :       "T1",
                    "LP" :      "T1",
                    "SCOW":       "T1",
                    "SOP":        "T1",
                    "SP" :       "T1",
                    "STONOQ" :      "T1",
                    "A":       "T1"
                    }

# Mapping
combined['Ticket_aggr'] = combined.Ticket_clean.map(Ticket_Dictionary)

sns.barplot(x='Ticket_aggr',y='Survived', data=combined)

### Missing Values

[[back to top](#Table-of-contents)]

#### Embarked

In [ ]:
# Embarked

# Get the null rows where Embarked is null
display(combined[combined.Embarked.isnull()][['Fare', 'Pclass', 'Embarked']])

# Embarked missing values
combined.boxplot(column='Fare', by=['Embarked','Pclass'], figsize=(8,6))
plt.axhline(y=80, color='blue')

# Remplace null values by C because most people who are Pclass 1 and Fare 80 has Embarked from C
combined = combined.set_value(combined.Embarked.isnull(), 'Embarked', 'C')

#### Fare

In [ ]:
# Fare

# Visualization of the fare which is missing
combined[combined.Fare.isnull()][['Pclass', 'Fare', 'Embarked']]
#df_test[(df_test.Pclass==3)&(df_test.Embarked=='S')].Fare.hist(bins=100)
combined.loc[(combined['Pclass']==3) & (combined['Embarked']=='S')].Fare.hist(bins=100,figsize=(8,6))

# Get and affect the median to the missing value
Fare_median=combined[(combined.Pclass==3) & (combined.Embarked=='S')].Fare.median()
#df_test = df_test.set_value(df_test.Fare.isnull(), 'Fare', Fare_median)
combined["Fare"].fillna(Fare_median, inplace=True)

#### Age with median

In [ ]:
# Simply fill the nan values with median using Sex, Pclass and Title
grouped = combined.groupby(['Sex','Pclass','Title_aggr'])
age_median = grouped['Age'].median()
display(age_median)
combined["Age"] = combined.groupby(['Sex','Pclass','Title_aggr'])['Age'].transform(lambda x: x.fillna(x.median()))

#### Verification of missing values

In [ ]:
combined.isnull().sum()

#### Split for visualization

In [ ]:
# Split
df_train, df_test, targets = recover_train_test_target(combined)

# Dropping Cabin, Ticket and PassengerId
df_train = df_train.drop(['Cabin','PassengerId','Ticket'], axis=1)
df_test = df_test.drop(['Cabin','Ticket'], axis=1)

In [ ]:
df_train.shape

In [ ]:
df_train.columns

### Visualization new Features

[[back to top](#Table-of-contents)]

#### Visualization Name

In [ ]:
# Vrack v1 a faire marcher
fig5, ((axis1,axis2),(axis3,axis4),(axis5,axis6),(axis7,axis8)) = plt.subplots(4,2,figsize=(15,15))

# Plot Name_Length
sns.countplot(x='Name_Length', data=df_train, ax=axis1)

# Plot Name_Length by mean of survival
sns.barplot(x='Name_Length', y='Survived', data=df_train, ax=axis2)

# Plot Name_Size by mean of survival
sns.barplot(x='Name_Size', data=df_train, order=["Short","Medium","Long","Very Long"], ax=axis3)

# Plot Name_Size by mean of survival
sns.barplot(x='Name_Size',y='Survived', data=df_train, order=["Short","Medium","Long","Very Long"], ax=axis4)

# Plot Title aggregate
sns.barplot(x='Title_aggr', data=df_train, ax=axis5)

# Display Title aggregate by mean of survival
sns.barplot(x='Title_aggr',y='Survived', data=df_train, ax=axis6)

# Display Title aggregate and Name Size by mean of survival
sns.barplot(x='Title_aggr',y='Survived', hue='Name_Size', data=df_train, ax=axis7)

# Display Title aggregate and Name Size by mean of survival
sns.barplot(x='Name_Size',y='Survived', hue='Title_aggr', data=df_train, ax=axis8)

In [ ]:
# Vrack v2 a faire marcher
fig = plt.figure(figsize=(15, 5))
fig=sns.countplot(x='Name_Length', data=df_train)

fig=sns.barplot(x='Name_Length', y='Survived', data=df_train)

sns.barplot(x='Name_Size',y='Survived', data=df_train, order=["Short","Medium","Long","Very Long"])

# Display aggregate title by survived probability
fig1 = plt.figure(figsize=(15, 5))
fig1=sns.barplot(x='Title_aggr',y='Survived', data=df_train)

# Display aggregate title and Name Size by survived probability
fig2 = plt.figure(figsize=(15, 5))
fig2=sns.barplot(x='Title_aggr',y='Survived', hue='Name_Size', data=df_train)

# Display aggregate title and Name Size by survived probability
fig3 = plt.figure(figsize=(15, 5))
fig3=sns.barplot(x='Name_Size',y='Survived', hue='Title_aggr', data=df_train)

#### Visualization Family

In [ ]:
# A afficher correctrement
fig1 = plt.figure(figsize=(15, 5))
fig1 = sns.countplot(x='Number_of_relatives', data=df_train)

fig2 = plt.figure(figsize=(15, 5))
fig2 = sns.barplot(x='Number_of_relatives',y='Survived', data=df_train)

sns.barplot(x='Size_Family',y='Survived', data=df_train, order=['Alone', 'Small', 'Big'])

# Number_of_relatives with Pclass, Sex, Embarked by mean of survival
fig7, ((axis1),(axis2),(axis3)) = plt.subplots(3,1,figsize=(20,20))
sns.barplot(x='Number_of_relatives',y='Survived',hue='Pclass', data=df_train, ax=axis1)
sns.barplot(x='Number_of_relatives',y='Survived',hue='Sex', data=df_train, ax=axis2)
sns.barplot(x='Number_of_relatives',y='Survived',hue='Embarked', data=df_train, ax=axis3)
fig7.suptitle("Cross Representation of the features linked to the target : Survived")

# Size_Family with Pclass, Sex, Embarked by mean of survival
fig8, ((axis1),(axis2),(axis3)) = plt.subplots(3,1,figsize=(20,20))
sns.barplot(x='Size_Family',y='Survived',hue='Pclass', data=df_train, order=['Alone', 'Small', 'Big'], ax=axis1,)
sns.barplot(x='Size_Family',y='Survived',hue='Sex', data=df_train, order=['Alone', 'Small', 'Big'], ax=axis2)
sns.barplot(x='Size_Family',y='Survived',hue='Embarked', data=df_train, order=['Alone', 'Small', 'Big'], ax=axis3)
fig8.suptitle("Cross Representation of the features linked to the target : Survived")

### Features Encoding

[[back to top](#Table-of-contents)]

In [ ]:
display(combined.columns)
display(combined.isnull().sum())
display(combined.shape)
display(combined[["Embarked","Sex","Title_aggr","Size_Family","Name_Size","Pclass"]].head())

#### Categorial features encoding

##### Label Encoding

In [ ]:
from sklearn.preprocessing import LabelEncoder

# Dataframe with numerical categorical feature
combined_num_cat = pd.DataFrame()

# LabelEncoder
labelEnc = LabelEncoder()

# Columns to apply
cat_vars=["Embarked","Sex","Title_aggr","Size_Family","Name_Size"]

for col in cat_vars:
    labelEnc.fit(np.unique(list(combined[col].values)))
    combined_num_cat[col]=labelEnc.transform(combined[col].astype('str'))
    
labelEnc.fit(np.unique(list(combined["Pclass"].values)))
combined_num_cat["Pclass"]=labelEnc.transform(combined["Pclass"].astype('int'))

In [ ]:
combined_num_cat.head()

##### One Hot  Encoding

In [ ]:
def one_hot(df_in, cols):
    df_out = pd.DataFrame()
    for each in cols:
        dummies = pd.get_dummies(df_in[each], prefix=each, drop_first=False)
        df_out = pd.concat([df_out, dummies], axis=1)
    return df_out

In [ ]:
# Dataframe with binary categorical feature

# Columns to apply
cat_vars=['Embarked','Sex',"Title_aggr","Size_Family","Name_Size","Pclass"]
combined_One_Hot_Cat = one_hot(combined,cat_vars)

In [ ]:
combined_One_Hot_Cat.head()

### Feature Scalling

[[back to top](#Table-of-contents)]

In [ ]:
combined[['Fare','Age','Name_Length','Number_of_relatives']].head()

In [ ]:
from sklearn import preprocessing

std_columns = ['Fare','Age']

combined_num_std = pd.DataFrame(combined[std_columns])

# StandardScaller process
std_scale = preprocessing.StandardScaler()
combined_num_std[std_columns] = std_scale.fit_transform(combined[std_columns].astype(float))

combined_num_std[std_columns].head()

### Data Preparation

[[back to top](#Table-of-contents)]

In [ ]:
# Concat
combined_OH_Std = pd.concat([combined_num_std,combined_One_Hot_Cat],axis=1)
combined_Num_Std = pd.concat([combined_num_std,combined_num_cat],axis=1)

In [ ]:
# Display shape
display(combined_OH_Std.shape)
display(combined_Num_Std.shape)

In [ ]:
# Split into Train and Eval
Train_OH_Std, Eval_OH_Std, Target_OH_Std = recover_train_test_target(combined_OH_Std)
Train_Num_Std, Eval_Num_Std, Target_Num_Std = recover_train_test_target(combined_Num_Std)

In [ ]:
# Display shape
display(Train_OH_Std.shape)
display(Eval_OH_Std.shape)
display(Target_OH_Std.shape)

In [ ]:
# Select Data
data = Train_OH_Std
test_data = Eval_OH_Std
target = Target_OH_Std
columns_name = list(Train_OH_Std)

# Train & Test
X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=0.20, random_state = 42,stratify=target)

# Dataframe of prediction
Prediction = pd.DataFrame()

pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_rows', 1000)

### Features Importance


[[back to top](#Table-of-contents)]

#### Correlation - Numerical label

In [ ]:
# Concant data and target
Features_with_target = pd.concat([Train_Num_Std,target],axis=1)
# Correlation with target
Corr = pd.DataFrame()
Corr['Corr'] = Features_with_target.corr()["Survived"]
Corr.sort_values('Corr',ascending=False,inplace=True)
display(Corr)
# A réfléchir au sens en regardant la formule de corr pour les catégories le numerical label ordinales et non ordinales

#### Correlation - One Hot Encoder

In [ ]:
# Concant data and target
Features_with_target = pd.concat([Train_OH_Std,target],axis=1)
# Correlation with target
Corr = pd.DataFrame()
Corr['Corr'] = Features_with_target.corr()["Survived"]
Corr.sort_values('Corr',ascending=False,inplace=True)
display(Corr)

#### LDA

In [ ]:
# LDA
# LDA with n = 2 solver svd --> score : 0.78947
lda = LinearDiscriminantAnalysis(n_components = 2, solver='svd')
lda.fit(X_train, y_train)

y_train_pred_lda = lda.predict(X_train)
y_test_pred_lda = lda.predict(X_test)

lda_acc = accuracy_score(y_test, y_test_pred_lda)
lda_cr= classification_report(y_test, y_test_pred_lda)
lda_cm = confusion_matrix(y_test, y_test_pred_lda)

lda_acc_train = accuracy_score(y_train, y_train_pred_lda)
lda_cr_train = classification_report(y_train, y_train_pred_lda)
lda_cm_train = confusion_matrix(y_train, y_train_pred_lda)

print("Training set")
print( "LDA Accuracy :", lda_acc_train)
print(lda_cr_train)
print("Confusion Matrix :\n",lda_cm_train)
#print('Explained variance ratio :',lda.explained_variance_ratio_)
print('Balance of classes',lda.priors_)

print("-----------------------------------------------------------------------------")
print("Testing set")
print( "LDA Accuracy :", lda_acc)
print(lda_cr)
print("Confusion Matrix :\n",lda_cm)
#print('Explained variance ratio :',lda.explained_variance_ratio_)
print('Balance of classes',lda.priors_)



Prediction['LDA'] = lda.predict(test_data)


Coef = pd.DataFrame()
Coef['Features'] = list(X_train.columns)
Coef['Coef'] = lda.coef_.transpose()
Coef.sort_values('Coef',ascending=False,inplace=True)
Coef

#### Features importance


In [ ]:
list(data.columns)

#### Anova

In [ ]:
# Select K Best 
from sklearn.feature_selection import SelectKBest,f_classif,chi2,SelectFpr,SelectFdr

# Perform feature selection
selector_anova = SelectKBest(f_classif, k="all")
#selector_chi2 = SelectKBest(chi2, k="all")

selector_anova.fit(data, target)
#selector_chi2.fit(data, target)

In [ ]:
# Get and display result
result_selector = pd.DataFrame()
result_selector['feature'] = list(data.columns)
result_selector['Anova score'] = selector_anova.scores_
result_selector['Anova pval'] = selector_anova.pvalues_
result_selector.sort_values('Anova score',ascending=False,inplace=True)
result_selector

### Features Selection

[[back to top](#Table-of-contents)]

In [ ]:
data.drop(['Title_aggr_Royalty','Title_aggr_Officer','Name_Size_Medium','Embarked_Q'],axis=1,inplace=True)
test_data.drop(['Title_aggr_Royalty','Title_aggr_Officer','Name_Size_Medium','Embarked_Q'],axis=1,inplace=True)

In [ ]:
display(data.shape)
test_data.shape

In [ ]:
# Train & Test
X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=0.20 ,random_state =42)

### Models Selection

[[back to top](#Table-of-contents)]

#### Helper function

In [ ]:
# Helper function to analyse and get result

# Plot the confusion matrice 
def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues):
    """
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')

    print(cm)

    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)

    fmt = '.2f' if normalize else 'd'
    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, format(cm[i, j], fmt),
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")

    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label')


# Grid Score into a Pandas Dataframe
def cv_results_to_df(cv_results):
    """
    Convert a sklearn.model_selection.GridSearchCV.cv_results_ attribute to a tidy
    pandas DataFrame where the output is filtered with only mean std and params.
    """
    df=pd.DataFrame.from_dict(cv_results)
    df=df[['mean_test_score', 'std_test_score', 'mean_train_score', 'std_train_score', 'params']]
    df.sort_values('mean_test_score',ascending=False,inplace=True)
    return df


# Helper function for gridseach
def grid_search_global(dict_pip, dict_param, class_names):

    dict_of_res={}
    dict_of_best={}
    df_results_global=pd.DataFrame()
    
    print ("Starting Gridsearch")
    
    for key in dict_param.keys():
        gs = GridSearchCV(dict_pip[key], dict_param[key], verbose=0, refit=True, n_jobs=-1, cv=5)
        gs = gs.fit(X_train, y_train)
        dict_of_res[key]=gs.grid_scores_
        
        print('\n-------------------------------------------------------------------------------------------------------')
        print ("Gridsearch for %s \n" % dict_param[key])
        print ("Best score :", gs.best_score_)
        print ("Best params :",gs.best_params_)
        dict_of_best[key]=[gs.best_score_,gs.best_params_]
        
        y_test_pred=gs.predict(X_test)
        validation_acc = accuracy_score(y_test,y_test_pred)
        validation_Fscore = f1_score(y_test,y_test_pred)
        
        
        
        # Obtention des résultats avec selection et réarrangement des attributs puis stockage
        df_results=cv_results_to_df(gs.cv_results_)
        df_results['Algo']=key
        df_results['Diff_train_test']=  np.absolute (df_results['mean_train_score'] - df_results['mean_test_score'])
        df_results['Val_Acc'] = validation_acc
        df_results['Diff_test_val']= np.absolute(df_results['mean_test_score'] - df_results['Val_Acc'])
        df_results['Val_F_score'] = validation_Fscore
        df_results=df_results[['Algo','Val_Acc','Diff_test_val','Diff_train_test','Val_F_score','mean_test_score', 'std_test_score', 'mean_train_score', 'std_train_score', 'params']]
        df_results_global=df_results_global.append(df_results)
        print("\nGrid Score #cv_results_ alégé")
        display(df_results)
        

        
    # Transformation de dict_of_best en dataframe
    df_best=pd.DataFrame.from_dict(dict_of_best,'index')
    df_best.columns=['Scores','Parameters']
    df_best.sort_values('Scores',ascending=False,inplace=True)  

    df_results_global.sort_values('Val_Acc',ascending=False,inplace=True)
    print('\n -------------------------------------------------------------------------------------------------------')
    print('\nList of best score and parameters by pipeline')
    display(df_best)
    print('\nSummary')
    display(df_results_global)
    print ("Gridsearch Finished")
    print('\n -------------------------------------------------------------------------------------------------------')    
    return df_best, dict_of_best, df_results_global



"""
========================
Plotting Learning Curves
========================
On the left side the learning curve of a naive Bayes classifier is shown for
the digits dataset. Note that the training score and the cross-validation score
are both not very good at the end. However, the shape of the curve can be found
in more complex datasets very often: the training score is very high at the
beginning and decreases and the cross-validation score is very low at the
beginning and increases. On the right side we see the learning curve of an SVM
with RBF kernel. We can see clearly that the training score is still around
the maximum and the validation score could be increased with more training
samples.
"""
print(__doc__)

import numpy as np
import matplotlib.pyplot as plt
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
from sklearn.datasets import load_digits
from sklearn.model_selection import learning_curve
from sklearn.model_selection import ShuffleSplit


def plot_learning_curve(estimator, title, X, y, ylim=None, cv=None,
                        n_jobs=1, train_sizes=np.linspace(.1, 1.0, 5)):
    """
    Generate a simple plot of the test and training learning curve.
    Parameters
    ----------
    estimator : object type that implements the "fit" and "predict" methods
        An object of that type which is cloned for each validation.
    title : string
        Title for the chart.
    X : array-like, shape (n_samples, n_features)
        Training vector, where n_samples is the number of samples and
        n_features is the number of features.
    y : array-like, shape (n_samples) or (n_samples, n_features), optional
        Target relative to X for classification or regression;
        None for unsupervised learning.
    ylim : tuple, shape (ymin, ymax), optional
        Defines minimum and maximum yvalues plotted.
    cv : int, cross-validation generator or an iterable, optional
        Determines the cross-validation splitting strategy.
        Possible inputs for cv are:
          - None, to use the default 3-fold cross-validation,
          - integer, to specify the number of folds.
          - An object to be used as a cross-validation generator.
          - An iterable yielding train/test splits.
        For integer/None inputs, if ``y`` is binary or multiclass,
        :class:`StratifiedKFold` used. If the estimator is not a classifier
        or if ``y`` is neither binary nor multiclass, :class:`KFold` is used.
        Refer :ref:`User Guide <cross_validation>` for the various
        cross-validators that can be used here.
    n_jobs : integer, optional
        Number of jobs to run in parallel (default 1).
    """
    plt.figure()
    plt.title(title)
    if ylim is not None:
        plt.ylim(0.7, 1)
    plt.xlabel("Training examples")
    plt.ylabel("Score")
    train_sizes, train_scores, test_scores = learning_curve(
        estimator, X, y, cv=cv, n_jobs=n_jobs, train_sizes=train_sizes)
    train_scores_mean = np.mean(train_scores, axis=1)
    train_scores_std = np.std(train_scores, axis=1)
    test_scores_mean = np.mean(test_scores, axis=1)
    test_scores_std = np.std(test_scores, axis=1)
    plt.grid()

    plt.fill_between(train_sizes, train_scores_mean - train_scores_std,
                     train_scores_mean + train_scores_std, alpha=0.1,
                     color="r")
    plt.fill_between(train_sizes, test_scores_mean - test_scores_std,
                     test_scores_mean + test_scores_std, alpha=0.1, color="g")
    plt.plot(train_sizes, train_scores_mean, 'o-', color="r",
             label="Training score")
    plt.plot(train_sizes, test_scores_mean, 'o-', color="g",
             label="Cross-validation score")

    plt.legend(loc="best")
    return plt

import matplotlib.pyplot as plt
import numpy as np
from sklearn.model_selection import validation_curve

def plot_validation_curve(estimator, estimator_name, param_name, param_range, X, y, cv,
    scoring='accuracy', scale='classic' , n_jobs=-1):
    
    train_scores, test_scores = validation_curve(
        estimator, X, y, param_name=param_name, param_range=param_range,
        cv=cv, scoring=scoring, n_jobs=n_jobs)

    train_scores_mean = np.mean(train_scores, axis=1)
    train_scores_std = np.std(train_scores, axis=1)
    test_scores_mean = np.mean(test_scores, axis=1)
    test_scores_std = np.std(test_scores, axis=1)
    
    title_fig='Validation Curve with %s' % estimator_name
    plt.title(title_fig)
    plt.xlabel(param_name)
    plt.ylabel("Score : %s" % scoring)
    plt.ylim(0.7, 1)
    lw = 2
    
    if (scale=='semilog'):
        plt.semilogx(param_range, train_scores_mean, label="Training score",
                     color="darkorange", lw=lw)
        plt.fill_between(param_range, train_scores_mean - train_scores_std,
                         train_scores_mean + train_scores_std, alpha=0.2,
                         color="darkorange", lw=lw)
        plt.semilogx(param_range, test_scores_mean, label="Cross-validation score",
                     color="navy", lw=lw)
        plt.fill_between(param_range, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.2,
                         color="navy", lw=lw)
    else :
        plt.plot(param_range, train_scores_mean, label="Training score",
                     color="darkorange", lw=lw)
        plt.fill_between(param_range, train_scores_mean - train_scores_std,
                         train_scores_mean + train_scores_std, alpha=0.2,
                         color="darkorange", lw=lw)
        plt.plot(param_range, test_scores_mean, label="Cross-validation score",
                     color="navy", lw=lw)
        plt.fill_between(param_range, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.2,
                         color="navy", lw=lw) 

    plt.legend(loc="best")
    plt.show()
    




### Multipes Algo

In [ ]:
# Pipeline setup
models = { 
    'RandomForestClassifier': RandomForestClassifier(),
    'GradientBoostingClassifier': GradientBoostingClassifier(),
    'SVC': SVC()
}

# Parameters setup
params = {
    # Il faut mettre 'ExtraTreesClassifier__n_estimators' dans 'ExtraTreesClassifier' car on est sur un pipeline 
    # il est donc possible de préciser des parametres pour chacune des étapes
    'RandomForestClassifier': { 'n_estimators': [5, 10, 15, 20, 25, 30, 35] },
    'GradientBoostingClassifier': { 'n_estimators': [5, 10, 15, 20, 25, 30, 35], 'learning_rate': [0.8, 1.0] },
    'SVC': [
        {'kernel': ['linear'], 'C': [1, 10]},
        {'kernel': ['rbf'], 'C': [1, 10], 'gamma': [0.001, 0.0001]},
    ]
}

# Lancer la grid search
df_best, dic_best, d_res =grid_search_global('clas',models,params,class_names=columns_name)

### Gradient Boosting Classifier

[[back to top](#Table-of-contents)]

In [ ]:
X_train.shape

In [ ]:
Res_gbc  =pd.DataFrame()
Res_rf  =pd.DataFrame()

for i in range(1,100) :
    print('Step',i)
    RS = np.random.randint(10000)

    X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=0.20,random_state = RS,stratify=target)

    # Pipeline setup
    model_gbc = { 
        'GradientBoostingClassifier': GradientBoostingClassifier(),
    }

    # Parameters setup
    params_gbc = {
        'GradientBoostingClassifier': { 'n_estimators': [5,10,15,20], 
                                       'learning_rate': [0.05,0.1,0.2],
                                      'loss' : ['deviance','exponential'],
                                      'max_depth' : [3],
                                       'min_samples_split': [3,5,7],
                                       'min_samples_leaf' : [3,5,7],
                                       'max_features' : [2,4,6,8,10]
                                      }
    }

    # Lancer la grid search
    df_best_gbc, dic_best_gbc, d_res_gbc =grid_search_global(model_gbc,params_gbc,class_names=columns_name)

    model_rf = { 
    'RandomForestClassifier': RandomForestClassifier(),
    }

    # Parameters setup
    params_rf = {
    # Il faut mettre 'ExtraTreesClassifier__n_estimators' dans 'ExtraTreesClassifier' car on est sur un pipeline 
    # il est donc possible de préciser des parametres pour chacune des étapes
    'RandomForestClassifier': { 'n_estimators': [5,10,15,20,30],
                               'criterion' : ['gini','entropy'],
                               'max_depth' : [3,9,15,30],
                               'max_features':[2,4,6,8],
                               'min_samples_split': [3,5,7],
                               'min_samples_leaf':  [3,5,7]
                              }
    }

    # Lancer la grid search
    df_best_rf, dic_best_rf, d_res_rf =grid_search_global(model_rf,params_rf,class_names=columns_name)

    # Results dataframe
    d_res_gbc['Random_state'] = RS
    d_res_gbc.sort_values(by=['Val_Acc','std_test_score'],ascending=[False,True],inplace=True)
    d_res_gbc_sort = d_res_gbc.loc[(d_res_gbc['Val_Acc'] > 0.80) 
                  & (d_res_gbc['Diff_test_val'] < 0.01) 
                  & (d_res_gbc['Diff_train_test'] < 0.01)  
                  & (d_res_gbc['std_test_score'] < 0.01) 
                  & (d_res_gbc['std_train_score'] < 0.01)]
    Res_gbc = Res_gbc.append(d_res_gbc_sort)
    
    # Results dataframe
    d_res_rf['Random_state'] = RS
    d_res_rf.sort_values(by=['Val_Acc','std_test_score'],ascending=[False,True],inplace=True)
    d_res_rf_sort = d_res_rf.loc[(d_res_rf['Val_Acc'] > 0.80) 
                  & (d_res_rf['Diff_test_val'] < 0.01) 
                  & (d_res_rf['Diff_train_test'] < 0.01)  
                  & (d_res_rf['std_test_score'] < 0.01) 
                  & (d_res_rf['std_train_score'] < 0.01)]
    Res_rf = Res_rf.append(d_res_rf_sort)   


In [108]:
Res

Algo   Val_Acc  Diff_test_val  Diff_train_test  \
246  GradientBoostingClassifier  0.815642  0.000369       0.006665          
488  GradientBoostingClassifier  0.815642  0.008058       0.008767          
133  GradientBoostingClassifier  0.815642  0.012272       0.009473          
301  GradientBoostingClassifier  0.815642  0.010867       0.002098          
141  GradientBoostingClassifier  0.815642  0.006654       0.000702          
77   GradientBoostingClassifier  0.815642  0.010867       0.004558          
137  GradientBoostingClassifier  0.815642  0.013676       0.004206          
329  GradientBoostingClassifier  0.815642  0.006654       0.002095          
153  GradientBoostingClassifier  0.815642  0.003845       0.004202          
468  GradientBoostingClassifier  0.815642  0.013676       0.012986          
472  GradientBoostingClassifier  0.815642  0.013676       0.012986          
7    GradientBoostingClassifier  0.815642  0.005249       0.009127          
11   GradientBoostingClassifier  0.815642  0.005249       0.008776          
609  GradientBoostingClassifier  0.815642  0.005987       0.009483          
484  GradientBoostingClassifier  0.815642  0.012272       0.006680          
38   GradientBoostingClassifier  0.815642  0.002440       0.009116          
113  GradientBoostingClassifier  0.815642  0.010867       0.009116          
357  GradientBoostingClassifier  0.815642  0.002440       0.002447          
349  GradientBoostingClassifier  0.815642  0.002440       0.002447          
476  GradientBoostingClassifier  0.815642  0.013676       0.008065          
230  GradientBoostingClassifier  0.815642  0.005249       0.010522          
692  GradientBoostingClassifier  0.815642  0.013676       0.010168          
58   GradientBoostingClassifier  0.815642  0.002440       0.008073          
472  GradientBoostingClassifier  0.815642  0.009463       0.010530          
85   GradientBoostingClassifier  0.815642  0.013676       0.003504          
165  GradientBoostingClassifier  0.815642  0.003845       0.002799          
700  GradientBoostingClassifier  0.815642  0.012272       0.002810          
309  GradientBoostingClassifier  0.815642  0.010867       0.001757          
541  GradientBoostingClassifier  0.815642  0.005249       0.011576          
520  GradientBoostingClassifier  0.815642  0.009463       0.007359          
81   GradientBoostingClassifier  0.815642  0.003845       0.000347          
153  GradientBoostingClassifier  0.815642  0.006654       0.003853          
203  GradientBoostingClassifier  0.815642  0.001036       0.000702          
317  GradientBoostingClassifier  0.815642  0.013676       0.006670          
341  GradientBoostingClassifier  0.815642  0.008058       0.005962          
301  GradientBoostingClassifier  0.815642  0.010867       0.001402          
708  GradientBoostingClassifier  0.815642  0.010867       0.003852          
271  GradientBoostingClassifier  0.815642  0.010200       0.013687          
117  GradientBoostingClassifier  0.815642  0.010867       0.008423          
373  GradientBoostingClassifier  0.815642  0.000369       0.012275          
97   GradientBoostingClassifier  0.815642  0.005249       0.005268          
121  GradientBoostingClassifier  0.815642  0.008058       0.007011          
652  GradientBoostingClassifier  0.815642  0.012272       0.005958          
386  GradientBoostingClassifier  0.815642  0.010200       0.008068          
18   GradientBoostingClassifier  0.815642  0.013676       0.004909          
66   GradientBoostingClassifier  0.815642  0.001036       0.014043          
187  GradientBoostingClassifier  0.815642  0.001036       0.009126          
169  GradientBoostingClassifier  0.815642  0.008058       0.007715          
609  GradientBoostingClassifier  0.815642  0.005987       0.006668          

     Val_F_score  mean_test_score  std_test_score  mean_train_score  \
246  0.740157     0.816011         0.004392        0.822676           
488  0.740157     0.807584        

In [115]:
# Train & Test
X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=0.20,random_state = 6725,stratify=target)

In [116]:
# Pipeline setup
models = { 
    'GradientBoostingClassifier': GradientBoostingClassifier(),
}

# Parameters setup
params = {
    'GradientBoostingClassifier': { 'n_estimators': [5,10,15,20,50,100,250,500], 
                                   'learning_rate': [0.01,0.05,0.1,0.2],
                                  'loss' : ['deviance','exponential'],
                                    'max_depth' : [3,5,7,10],
                                   'min_samples_split': [3,5,7],
                                   'min_samples_leaf' : [3,5,7],
                                   'max_features' : [2,4,6,8,10]
                                  }
}

# Lancer la grid search
df_best_gbc, dic_best_gbc, d_res_gbc =grid_search_global(models,params,class_names=columns_name)

Starting Gridsearch

-------------------------------------------------------------------------------------------------------
Gridsearch for {'n_estimators': [5, 10, 15, 20, 50, 100, 250, 500], 'learning_rate': [0.01, 0.05, 0.1, 0.2], 'loss': ['deviance', 'exponential'], 'max_depth': [3, 5, 7, 10], 'min_samples_split': [3, 5, 7], 'min_samples_leaf': [3, 5, 7], 'max_features': [2, 4, 6, 8, 10]} 

Best score : 0.842696629213
Best params : {'learning_rate': 0.05, 'loss': 'exponential', 'max_depth': 3, 'max_features': 6, 'min_samples_leaf': 3, 'min_samples_split': 3, 'n_estimators': 20}

Grid Score #cv_results_ alégé


Algo   Val_Acc  Diff_test_val  Diff_train_test  \
4467   GradientBoostingClassifier  0.810056  0.032641       2.816694e-03      
181    GradientBoostingClassifier  0.810056  0.031236       6.322761e-03      
4475   GradientBoostingClassifier  0.810056  0.031236       5.267665e-03      
5994   GradientBoostingClassifier  0.810056  0.029832       8.428393e-03      
1669   GradientBoostingClassifier  0.810056  0.029832       8.081211e-03      
7948   GradientBoostingClassifier  0.810056  0.029832       6.671848e-02      
3147   GradientBoostingClassifier  0.810056  0.028427       9.489397e-03      
5993   GradientBoostingClassifier  0.810056  0.028427       8.080353e-03      
4850   GradientBoostingClassifier  0.810056  0.028427       1.439738e-02      
5893   GradientBoostingClassifier  0.810056  0.028427       4.425157e-02      
7470   GradientBoostingClassifier  0.810056  0.028427       9.340035e-02      
3165   GradientBoostingClassifier  0.810056  0.028427       3.792345e-02      
4591   GradientBoostingClassifier  0.810056  0.028427       9.199683e-02      
8633   GradientBoostingClassifier  0.810056  0.028427       5.372897e-02      
9420   GradientBoostingClassifier  0.810056  0.028427       8.743050e-02      
3003   GradientBoostingClassifier  0.810056  0.028427       3.515233e-03      
9856   GradientBoostingClassifier  0.810056  0.027023       2.739809e-02      
1701   GradientBoostingClassifier  0.810056  0.027023       1.159011e-02      
149    GradientBoostingClassifier  0.810056  0.027023       1.159134e-02      
4503   GradientBoostingClassifier  0.810056  0.027023       8.953736e-02      
7388   GradientBoostingClassifier  0.810056  0.027023       2.914817e-02      
229    GradientBoostingClassifier  0.810056  0.027023       1.299239e-02      
269    GradientBoostingClassifier  0.810056  0.027023       1.088897e-02      
4427   GradientBoostingClassifier  0.810056  0.027023       1.051451e-03      
4395   GradientBoostingClassifier  0.810056  0.027023       1.058221e-03      
4383   GradientBoostingClassifier  0.810056  0.027023       4.916668e-02      
4358   GradientBoostingClassifier  0.810056  0.027023       3.582162e-02      
9840   GradientBoostingClassifier  0.810056  0.027023       2.949412e-02      
7601   GradientBoostingClassifier  0.810056  0.027023       1.299054e-02      
2971   GradientBoostingClassifier  0.810056  0.027023       8.783083e-03      
3996   GradientBoostingClassifier  0.810056  0.027023       6.074874e-02      
5163   GradientBoostingClassifier  0.810056  0.027023       3.054861e-02      
7714   GradientBoostingClassifier  0.810056  0.027023       4.179024e-02      
5258   GradientBoostingClassifier  0.810056  0.027023       5.583584e-02      
5883   GradientBoostingClassifier  0.810056  0.027023       8.781849e-03      
10189  GradientBoostingClassifier  0.810056  0.027023       6.320734e-02      
4607   GradientBoostingClassifier  0.810056  0.027023       9.340194e-02      
4597   GradientBoostingClassifier  0.810056  0.027023       3.721652e-02      
11210  GradientBoostingClassifier  0.810056  0.027023       4.389491e-02      
7262   GradientBoostingClassifier  0.810056  0.027023       5.021439e-02      
4599   GradientBoostingClassifier  0.810056  0.027023       9.304922e-02      
8899   GradientBoostingClassifier  0.810056  0.027023       2.704291e-02      
8307   GradientBoostingClassifier  0.810056  0.027023       4.916114e-02      
9128   GradientBoostingClassifier  0.810056  0.027023       1.615768e-02      
4540   GradientBoostingClassifier  0.810056  0.027023       2.212507e-02      
109    GradientBoostingClassifier  0.810056  0.025618       9.828696e-03      
10330  GradientBoostingClassifier  0.810056  0.025618       2.072438e-02      
7024   GradientBoostingClassifier  0.810056  0.025618       2.985029e-02      
7050   GradientBoostingClassifier  0.810056  0.025618       6.215139e-02      
5570   GradientBoostingClassifier  0.810056  0.025618       5.091775e-02      



 -------------------------------------------------------------------------------------------------------

List of best score and parameters by pipeline


Scores  \
GradientBoostingClassifier  0.842697   

                                                                                                                                                                      Parameters  
GradientBoostingClassifier  {'learning_rate': 0.05, 'loss': 'exponential', 'max_depth': 3, 'max_features': 6, 'min_samples_leaf': 3, 'min_samples_split': 3, 'n_estimators': 20}


Summary


Algo   Val_Acc  Diff_test_val  Diff_train_test  \
4467   GradientBoostingClassifier  0.810056  0.032641       2.816694e-03      
6400   GradientBoostingClassifier  0.810056  0.001067       3.441312e-02      
7799   GradientBoostingClassifier  0.810056  0.001067       1.811817e-01      
7241   GradientBoostingClassifier  0.810056  0.001067       1.438969e-02      
4014   GradientBoostingClassifier  0.810056  0.001067       1.523906e-01      
10138  GradientBoostingClassifier  0.810056  0.001067       2.950084e-02      
9349   GradientBoostingClassifier  0.810056  0.001067       1.688905e-01      
6534   GradientBoostingClassifier  0.810056  0.001067       1.643279e-01      
6390   GradientBoostingClassifier  0.810056  0.001067       1.724030e-01      
4269   GradientBoostingClassifier  0.810056  0.001067       1.766154e-01      
3583   GradientBoostingClassifier  0.810056  0.001067       1.734575e-01      
7211   GradientBoostingClassifier  0.810056  0.001067       3.196130e-02      
6557   GradientBoostingClassifier  0.810056  0.001067       1.667840e-01      
7760   GradientBoostingClassifier  0.810056  0.001067       1.895973e-02      
7203   GradientBoostingClassifier  0.810056  0.001067       3.266367e-02      
7258   GradientBoostingClassifier  0.810056  0.001067       2.212378e-02      
7838   GradientBoostingClassifier  0.810056  0.001067       1.727539e-01      
9177   GradientBoostingClassifier  0.810056  0.001067       7.303434e-02      
9182   GradientBoostingClassifier  0.810056  0.001067       1.811817e-01      
5142   GradientBoostingClassifier  0.810056  0.001067       1.622158e-01      
4230   GradientBoostingClassifier  0.810056  0.001067       1.804787e-01      
1303   GradientBoostingClassifier  0.810056  0.001067       1.745101e-01      
3710   GradientBoostingClassifier  0.810056  0.001067       1.639745e-01      
181    GradientBoostingClassifier  0.810056  0.031236       6.322761e-03      
9891   GradientBoostingClassifier  0.810056  0.001067       1.397406e-01      
6637   GradientBoostingClassifier  0.810056  0.001067       1.734550e-01      
5493   GradientBoostingClassifier  0.810056  0.001067       1.622183e-01      
5425   GradientBoostingClassifier  0.810056  0.001067       2.598652e-02      
5497   GradientBoostingClassifier  0.810056  0.001067       4.038299e-02      
6632   GradientBoostingClassifier  0.810056  0.001067       6.495738e-02      
8525   GradientBoostingClassifier  0.810056  0.001067       1.808302e-01      
3766   GradientBoostingClassifier  0.810056  0.001067       1.773165e-01      
6478   GradientBoostingClassifier  0.810056  0.001067       1.734581e-01      
8998   GradientBoostingClassifier  0.810056  0.001067       1.587114e-01      
6392   GradientBoostingClassifier  0.810056  0.001067       3.266060e-02      
9030   GradientBoostingClassifier  0.810056  0.001067       1.660810e-01      
6597   GradientBoostingClassifier  0.810056  0.001067       1.573029e-01      
7101   GradientBoostingClassifier  0.810056  0.001067       1.808302e-01      
5158   GradientBoostingClassifier  0.810056  0.001067       1.646757e-01      
9792   GradientBoostingClassifier  0.810056  0.001067       9.058748e-02      
11499  GradientBoostingClassifier  0.810056  0.001067       1.362373e-01      
8353   GradientBoostingClassifier  0.810056  0.001067       9.270382e-02      
6454   GradientBoostingClassifier  0.810056  0.001067       1.783716e-01      
5231   GradientBoostingClassifier  0.810056  0.001067       1.811817e-01      
9093   GradientBoostingClassifier  0.810056  0.001067       1.618674e-01      
10853  GradientBoostingClassifier  0.810056  0.001067       1.492315e-01      
8485   GradientBoostingClassifier  0.810056  0.001067       1.748585e-01      
4278   GradientBoostingClassifier  0.810056  0.001067       1.811817e-01      
10271  GradientBoostingClassifier  0.810056  0.001067       1.745101e-01      
6790   GradientBoostingClassifier  0.810056  0.001067       1.811817e-01      


Gridsearch Finished

 -------------------------------------------------------------------------------------------------------


In [ ]:
# Results dataframe
d_res_gbc.sort_values(by=['Val_Acc','std_test_score'],ascending=[False,True],inplace=True)
d_res_gbc_sort = d_res_gbc.loc[(d_res_gbc['Val_Acc'] > 0.80) 
              & (d_res_gbc['Diff_test_val'] < 0.015) 
              & (d_res_gbc['Diff_train_test'] < 0.015)  
              & (d_res_gbc['std_test_score'] < 0.015) 
              & (d_res_gbc['std_train_score'] < 0.015)]
d_res_gbc_sort

In [ ]:
# Pipeline setup
models = { 
    'GradientBoostingClassifier': GradientBoostingClassifier(),
}

# Parameters setup
params = {
    'GradientBoostingClassifier': { 'n_estimators': range(1,20,1), 
                                   'learning_rate': [0.05,0.08,0.10,0.12,0.14,0.16],
                                  'loss' : ['deviance','exponential'],
                                  'max_depth' : range(2,4),
                                   'min_samples_split': range(2,10,1),
                                   'min_samples_leaf' : range(2,10,1),
                                   'max_features' : range(1,15,1)
                                  }
}

# Lancer la grid search
df_best_gbc, dic_best_gbc, d_res_gbc =grid_search_global('clas',models,params,class_names=columns_name)

In [ ]:
# Selection of the parameters to study
index_selection = [177,130,106,63,87,86]
df_study = d_res.loc[index_selection,['Algo','params','mean_test_score','mean_train_score']]
df_study

In [ ]:
# Learning curve
index = list(df_study.index)
for ind in index :
    algo = df_study.loc[ind, 'Algo']
    params = df_study.loc[ind, 'params']
    mean_test = df_study.loc[ind, 'mean_test_score']
    mean_train = df_study.loc[ind, 'mean_train_score']
    title = "Learning Curves for the estimator %s which results are \n mean test:%s \n mean train %s \n with parameters %s)" % (algo,mean_test,mean_train,params)
    cv = ShuffleSplit(n_splits=50, test_size=0.2, random_state=0)
    estimator = models[algo]
    estimator.set_params(**params)
    plot_learning_curve(estimator, title, data, target, (0.3, 1.01), cv=cv, n_jobs=-1)
    plt.show()

In [ ]:
# Validation parameters setup
dict_Validation = { 
    'GradientBoostingClassifier':  { 'n_estimators': range(5,100,5), 
                                   'learning_rate': [0.01,0.03,0.1,0.2,0.3,0.4,0.5,0.6,0.7],
                                  'max_depth' : range(2,10,1),
                                   'min_samples_split': range(2,10,1),
                                   'min_samples_leaf' : range(2,10,1),
                                   'max_features' : range(2,19,1)
                                  } 
}

for ind in index :
    algo = df_study.loc[ind, 'Algo']
    params = df_study.loc[ind, 'params']
    mean_test = df_study.loc[ind, 'mean_test_score']
    mean_train = df_study.loc[ind, 'mean_train_score']
    print("Model: %s\nMean test: %s\nMean train: %s\nParams: %s" % (algo,mean_test,mean_train,params))
    estimator = models[algo]
    estimator.set_params(**params)
    cv = ShuffleSplit(n_splits=10, test_size=0.2, random_state=0)
    for key, value in dict_Validation[algo].items():
        plot_validation_curve(estimator, clef, key, value, X_train, y_train, scoring='accuracy', cv=cv)
        plt.show()

In [ ]:
# Prediction 
GBC_params =  {'learning_rate': 0.1, 'loss': 'deviance', 'max_depth': 3, 'max_features': 4, 'min_samples_leaf': 7, 'min_samples_split': 7, 'n_estimators': 10}
gbc = GradientBoostingClassifier(**GBC_params)
gbc.fit(X_train,y_train)
gbc_pred = gbc.predict(test_data)
Prediction['GBC'] = gbc_pred

### Random Forest Classifier

[[back to top](#Table-of-contents)]

In [114]:
# Pipeline setup
# data.drop(['Title_aggr_Royalty','Title_aggr_Officer','Name_Size_Medium','Embarked_Q'],axis=1,inplace=True)
# {'criterion': 'gini', 'max_features': 'sqrt', 'min_samples_leaf': 8, 'min_samples_split': 2, 'n_estimators': 30}
# Score 80.803 leader board, train with X_train or all data 

models = { 
    'RandomForestClassifier': RandomForestClassifier(),
}

# Parameters setup
params = {
    # Il faut mettre 'ExtraTreesClassifier__n_estimators' dans 'ExtraTreesClassifier' car on est sur un pipeline 
    # il est donc possible de préciser des parametres pour chacune des étapes
    'RandomForestClassifier': { 'n_estimators': [5,10,15,20,30,100],
                               'criterion' : ['gini','entropy'],
                               'max_depth' : [3,5,8,10,15,20],
                               'max_features':[2,4,6,8],
                               'min_samples_split': [3,5,7],
                               'min_samples_leaf':  [3,5,7]
                              }
}

# Lancer la grid search
df_best_rf, dic_best_rf, d_res_rf =grid_search_global(models,params,class_names=columns_name)

Starting Gridsearch

-------------------------------------------------------------------------------------------------------
Gridsearch for {'n_estimators': [5, 10, 15, 20, 30, 100], 'criterion': ['gini', 'entropy'], 'max_depth': [3, 5, 8, 10, 15, 20], 'max_features': [2, 4, 6, 8], 'min_samples_split': [3, 5, 7], 'min_samples_leaf': [3, 5, 7]} 

Best score : 0.838483146067
Best params : {'criterion': 'gini', 'max_depth': 10, 'max_features': 6, 'min_samples_leaf': 7, 'min_samples_split': 3, 'n_estimators': 10}

Grid Score #cv_results_ alégé


Algo   Val_Acc  Diff_test_val  Diff_train_test  \
793   RandomForestClassifier  0.804469  0.034014       0.019668          
2326  RandomForestClassifier  0.804469  0.032609       0.069521          
1059  RandomForestClassifier  0.804469  0.031205       0.044247          
510   RandomForestClassifier  0.804469  0.031205       0.015449          
2485  RandomForestClassifier  0.804469  0.031205       0.053019          
2047  RandomForestClassifier  0.804469  0.029800       0.014392          
1788  RandomForestClassifier  0.804469  0.029800       0.030542          
2074  RandomForestClassifier  0.804469  0.029800       0.031959          
2279  RandomForestClassifier  0.804469  0.029800       0.065665          
1599  RandomForestClassifier  0.804469  0.029800       0.012985          
2466  RandomForestClassifier  0.804469  0.029800       0.010879          
1855  RandomForestClassifier  0.804469  0.028396       0.031959          
2556  RandomForestClassifier  0.804469  0.028396       0.042145          
1866  RandomForestClassifier  0.804469  0.028396       0.030203          
325   RandomForestClassifier  0.804469  0.028396       0.021062          
2029  RandomForestClassifier  0.804469  0.028396       0.021415          
969   RandomForestClassifier  0.804469  0.028396       0.016862          
1153  RandomForestClassifier  0.804469  0.028396       0.017907          
1474  RandomForestClassifier  0.804469  0.028396       0.001406          
1472  RandomForestClassifier  0.804469  0.028396       0.003511          
1460  RandomForestClassifier  0.804469  0.028396       0.002108          
720   RandomForestClassifier  0.804469  0.028396       0.022822          
1094  RandomForestClassifier  0.804469  0.028396       0.032306          
1190  RandomForestClassifier  0.804469  0.028396       0.057236          
1088  RandomForestClassifier  0.804469  0.028396       0.029852          
213   RandomForestClassifier  0.804469  0.028396       0.003163          
125   RandomForestClassifier  0.804469  0.028396       0.002459          
914   RandomForestClassifier  0.804469  0.028396       0.006670          
650   RandomForestClassifier  0.804469  0.026991       0.040724          
1439  RandomForestClassifier  0.804469  0.026991       0.003159          
1848  RandomForestClassifier  0.804469  0.026991       0.042134          
2283  RandomForestClassifier  0.804469  0.026991       0.061443          
2513  RandomForestClassifier  0.804469  0.026991       0.040730          
134   RandomForestClassifier  0.804469  0.026991       0.001054          
2573  RandomForestClassifier  0.804469  0.026991       0.055130          
2258  RandomForestClassifier  0.804469  0.026991       0.016503          
1222  RandomForestClassifier  0.804469  0.026991       0.039325          
251   RandomForestClassifier  0.804469  0.026991       0.003164          
2529  RandomForestClassifier  0.804469  0.026991       0.024579          
714   RandomForestClassifier  0.804469  0.026991       0.034052          
1172  RandomForestClassifier  0.804469  0.026991       0.018261          
1575  RandomForestClassifier  0.804469  0.026991       0.016503          
1204  RandomForestClassifier  0.804469  0.026991       0.062152          
1202  RandomForestClassifier  0.804469  0.026991       0.066716          
1135  RandomForestClassifier  0.804469  0.026991       0.045643          
835   RandomForestClassifier  0.804469  0.026991       0.044596          
208   RandomForestClassifier  0.804469  0.026991       0.002812          
2005  RandomForestClassifier  0.804469  0.026991       0.045646          
2037  RandomForestClassifier  0.804469  0.026991       0.023880          
214   RandomForestClassifier  0.804469  0.026991       0.002811          
2379  RandomForestClassifier  0.804469  0.026991       0.033715          
1678  RandomForestClassifier  0.804469  0.026991       0.026335          
649   RandomForestClassifier  0.804469  0.026991       0.040031          
682   RandomForestClassifier


 -------------------------------------------------------------------------------------------------------

List of best score and parameters by pipeline


Scores  \
RandomForestClassifier  0.838483   

                                                                                                                                          Parameters  
RandomForestClassifier  {'criterion': 'gini', 'max_depth': 10, 'max_features': 6, 'min_samples_leaf': 7, 'min_samples_split': 3, 'n_estimators': 10}


Summary


Algo   Val_Acc  Diff_test_val  Diff_train_test  \
793   RandomForestClassifier  0.804469  0.034014       0.019668          
506   RandomForestClassifier  0.804469  0.012946       0.040382          
661   RandomForestClassifier  0.804469  0.012946       0.045297          
1985  RandomForestClassifier  0.804469  0.012946       0.025629          
1982  RandomForestClassifier  0.804469  0.012946       0.019665          
2080  RandomForestClassifier  0.804469  0.012946       0.056541          
575   RandomForestClassifier  0.804469  0.012946       0.051616          
1921  RandomForestClassifier  0.804469  0.012946       0.060397          
2221  RandomForestClassifier  0.804469  0.012946       0.060745          
2361  RandomForestClassifier  0.804469  0.012946       0.049515          
525   RandomForestClassifier  0.804469  0.012946       0.031603          
523   RandomForestClassifier  0.804469  0.012946       0.029841          
2585  RandomForestClassifier  0.804469  0.012946       0.051972          
401   RandomForestClassifier  0.804469  0.012946       0.041786          
511   RandomForestClassifier  0.804469  0.012946       0.037918          
1864  RandomForestClassifier  0.804469  0.012946       0.053732          
1862  RandomForestClassifier  0.804469  0.012946       0.049157          
2223  RandomForestClassifier  0.804469  0.012946       0.064612          
2366  RandomForestClassifier  0.804469  0.012946       0.046349          
2070  RandomForestClassifier  0.804469  0.012946       0.046360          
627   RandomForestClassifier  0.804469  0.012946       0.054083          
1977  RandomForestClassifier  0.804469  0.012946       0.028090          
2104  RandomForestClassifier  0.804469  0.012946       0.042487          
81    RandomForestClassifier  0.804469  0.012946       0.004214          
1942  RandomForestClassifier  0.804469  0.012946       0.050212          
2197  RandomForestClassifier  0.804469  0.012946       0.017902          
1935  RandomForestClassifier  0.804469  0.012946       0.051272          
1929  RandomForestClassifier  0.804469  0.012946       0.046358          
577   RandomForestClassifier  0.804469  0.012946       0.037928          
610   RandomForestClassifier  0.804469  0.012946       0.076205          
157   RandomForestClassifier  0.804469  0.012946       0.009488          
115   RandomForestClassifier  0.804469  0.012946       0.015106          
656   RandomForestClassifier  0.804469  0.012946       0.047049          
111   RandomForestClassifier  0.804469  0.012946       0.012639          
642   RandomForestClassifier  0.804469  0.012946       0.040388          
105   RandomForestClassifier  0.804469  0.012946       0.009131          
2013  RandomForestClassifier  0.804469  0.012946       0.063208          
630   RandomForestClassifier  0.804469  0.012946       0.040377          
2003  RandomForestClassifier  0.804469  0.012946       0.068475          
2367  RandomForestClassifier  0.804469  0.012946       0.052676          
2372  RandomForestClassifier  0.804469  0.012946       0.051622          
2326  RandomForestClassifier  0.804469  0.032609       0.069521          
2373  RandomForestClassifier  0.804469  0.012946       0.044596          
1476  RandomForestClassifier  0.804469  0.012946       0.018263          
1681  RandomForestClassifier  0.804469  0.012946       0.045292          
795   RandomForestClassifier  0.804469  0.012946       0.038970          
1330  RandomForestClassifier  0.804469  0.012946       0.007723          
1658  RandomForestClassifier  0.804469  0.012946       0.027729          
1209  RandomForestClassifier  0.804469  0.012946       0.054429          
246   RandomForestClassifier  0.804469  0.012946       0.022823          
1306  RandomForestClassifier  0.804469  0.012946       0.005271          
1670  RandomForestClassifier  0.804469  0.012946       0.026684          
853   RandomForestClassifier  0.804469  0.012946       0.041431          
247   RandomForestClassifier

Gridsearch Finished

 -------------------------------------------------------------------------------------------------------


In [113]:
# Results dataframe
d_res_rf

Algo   Val_Acc  Diff_test_val  Diff_train_test  \
1820  RandomForestClassifier  0.804469  0.032609       0.011934          
321   RandomForestClassifier  0.804469  0.012946       0.023172          
1088  RandomForestClassifier  0.804469  0.012946       0.048796          
384   RandomForestClassifier  0.804469  0.012946       0.037573          
1092  RandomForestClassifier  0.804469  0.012946       0.037561          
1623  RandomForestClassifier  0.804469  0.012946       0.041782          
865   RandomForestClassifier  0.804469  0.012946       0.056887          
1628  RandomForestClassifier  0.804469  0.012946       0.038274          
1629  RandomForestClassifier  0.804469  0.012946       0.036511          
254   RandomForestClassifier  0.804469  0.012946       0.017550          
1104  RandomForestClassifier  0.804469  0.012946       0.023171          
1431  RandomForestClassifier  0.804469  0.012946       0.019659          
855   RandomForestClassifier  0.804469  0.012946       0.049166          
2254  RandomForestClassifier  0.804469  0.012946       0.034762          
1425  RandomForestClassifier  0.804469  0.012946       0.017561          
283   RandomForestClassifier  0.804469  0.012946       0.028445          
1064  RandomForestClassifier  0.804469  0.012946       0.042134          
398   RandomForestClassifier  0.804469  0.012946       0.039678          
942   RandomForestClassifier  0.804469  0.012946       0.034072          
382   RandomForestClassifier  0.804469  0.012946       0.050564          
1606  RandomForestClassifier  0.804469  0.012946       0.028441          
1603  RandomForestClassifier  0.804469  0.012946       0.024924          
1465  RandomForestClassifier  0.804469  0.012946       0.019313          
2300  RandomForestClassifier  0.804469  0.012946       0.053380          
596   RandomForestClassifier  0.804469  0.012946       0.074789          
822   RandomForestClassifier  0.804469  0.012946       0.069882          
937   RandomForestClassifier  0.804469  0.012946       0.041787          
1069  RandomForestClassifier  0.804469  0.012946       0.043196          
1070  RandomForestClassifier  0.804469  0.012946       0.043545          
369   RandomForestClassifier  0.804469  0.012946       0.027382          
919   RandomForestClassifier  0.804469  0.012946       0.068122          
376   RandomForestClassifier  0.804469  0.012946       0.032304          
1590  RandomForestClassifier  0.804469  0.012946       0.022815          
2148  RandomForestClassifier  0.804469  0.012946       0.042840          
1458  RandomForestClassifier  0.804469  0.012946       0.016152          
909   RandomForestClassifier  0.804469  0.012946       0.022470          
1079  RandomForestClassifier  0.804469  0.012946       0.050213          
279   RandomForestClassifier  0.804469  0.012946       0.029489          
271   RandomForestClassifier  0.804469  0.012946       0.033001          
1000  RandomForestClassifier  0.804469  0.012946       0.054079          
994   RandomForestClassifier  0.804469  0.012946       0.056887          
2056  RandomForestClassifier  0.804469  0.032609       0.057945          
1527  RandomForestClassifier  0.804469  0.012946       0.022465          
962   RandomForestClassifier  0.804469  0.012946       0.032311          
368   RandomForestClassifier  0.804469  0.012946       0.032298          
1570  RandomForestClassifier  0.804469  0.012946       0.029843          
286   RandomForestClassifier  0.804469  0.012946       0.032650          
1063  RandomForestClassifier  0.804469  0.012946       0.045652          
1643  RandomForestClassifier  0.804469  0.012946       0.035813          
2234  RandomForestClassifier  0.804469  0.012946       0.037571          
243   RandomForestClassifier  0.804469  0.012946       0.024229          
2067  RandomForestClassifier  0.804469  0.012946       0.074096          
247   RandomForestClassifier  0.804469  0.012946       0.017206          
441   RandomForestClassifier

In [ ]:
# Pipeline setup
# data.drop(['Title_aggr_Royalty','Title_aggr_Officer','Name_Size_Medium','Embarked_Q'],axis=1,inplace=True)
# {'criterion': 'gini', 'max_features': 'sqrt', 'min_samples_leaf': 8, 'min_samples_split': 2, 'n_estimators': 30}
# Score 80.803 leader board, train with X_train or all data 

models = { 
    'RandomForestClassifier': RandomForestClassifier(),
}

# Parameters setup
params = {
    # Il faut mettre 'ExtraTreesClassifier__n_estimators' dans 'ExtraTreesClassifier' car on est sur un pipeline 
    # il est donc possible de préciser des parametres pour chacune des étapes
    'RandomForestClassifier': { 'n_estimators': range(1,20,1),
                               'criterion' : ['gini','entropy'],
                               'max_features':range(1,20,1),
                               'min_samples_split': range(2,10,1),
                               'min_samples_leaf':  range(1,10,1)
                              }
}

# Lancer la grid search
df_best_rf, dic_best_rf, d_res_rf =grid_search_global('clas',models,params,class_names=columns_name)

In [ ]:
# Selection of the parameters to study
index_selection = [707,102,199,1031]
df_study_rf = d_res_rf.loc[index_selection,['Algo','params','mean_test_score','mean_train_score']]
df_study_rf

In [ ]:
# Learning curve
index = list(df_study_rf.index)
for ind in index :
    algo = df_study_rf.loc[ind, 'Algo']
    params = df_study_rf.loc[ind, 'params']
    mean_test = df_study_rf.loc[ind, 'mean_test_score']
    mean_train = df_study_rf.loc[ind, 'mean_train_score']
    title = "Learning Curves for the estimator %s which results are \n mean test:%s \n mean train %s \n with parameters %s)" % (algo,mean_test,mean_train,params)
    cv = ShuffleSplit(n_splits=50, test_size=0.2, random_state=0)
    estimator = models[algo]
    estimator.set_params(**params)
    plot_learning_curve(estimator, title, data, target, (0.3, 1.01), cv=cv, n_jobs=-1)
    plt.show()

In [ ]:
# Validation parameters setup
dict_Validation = { 
    'RandomForestClassifier': {'n_estimators': range(1,50,2),
                               'max_features':range(1,20,1),
                                  'min_samples_split': range(2,10,1),
                                  'min_samples_leaf': range(2,10,1)}  
}

for ind in index :
    algo = df_study_rf.loc[ind, 'Algo']
    params = df_study_rf.loc[ind, 'params']
    mean_test = df_study_rf.loc[ind, 'mean_test_score']
    mean_train = df_study_rf.loc[ind, 'mean_train_score']
    print("Model: %s\nMean test: %s\nMean train: %s\nParams: %s" % (algo,mean_test,mean_train,params))
    estimator = models[algo]
    estimator.set_params(**params)
    cv = ShuffleSplit(n_splits=10, test_size=0.2, random_state=0)
    for key, value in dict_Validation[algo].items():
        plot_validation_curve(estimator, algo, key, value, X_train, y_train, scoring='accuracy', cv=cv)
        plt.show()

In [ ]:
# Prediction 
RF_params =  {'criterion': 'entropy', 'max_features': 12, 'min_samples_leaf': 1, 'min_samples_split': 8, 'n_estimators': 10}
rf = RandomForestClassifier(**RF_params)
rf.fit(X_train,y_train)
rf_pred = rf.predict(test_data)
Prediction['RF'] = rf_pred

In [ ]:
# Get and display result
Rf_feat_imp = pd.DataFrame()
Rf_feat_imp['Feature'] = list(data.columns)
Rf_feat_imp['Importance'] = rf.feature_importances_
Rf_feat_imp.sort_values('Importance',ascending=False,inplace=True)
Rf_feat_imp

In [ ]:
# From Random Forest
importances=rf.feature_importances_
plt.figure(figsize=(10,10))
plt.title("Feature Importances By Random Forest Model")
plt.bar(range(np.size(importances)), importances, align="center")
plt.xticks(range(np.size(importances)),list(data.columns),rotation='vertical')
plt.show()

### Adaboost

[[back to top](#Table-of-contents)]

In [ ]:
# Pipeline setup
models = { 
    'AdaBoostClassifier': AdaBoostClassifier(),
}

# Parameters setup
params = {
    # Il faut mettre 'ExtraTreesClassifier__n_estimators' dans 'ExtraTreesClassifier' car on est sur un pipeline 
    # il est donc possible de préciser des parametres pour chacune des étapes
    'AdaBoostClassifier': { 'n_estimators': [5, 10, 20, 30, 40, 50 ,100, 500 ],
                               'learning_rate' : [0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9,1],
                              }
}

# Lancer la grid search
df_best, dic_best, d_res =grid_search_global('clas',models,params,class_names=columns_name)

In [ ]:
# Prediction
ab_params = {'learning_rate': 0.3, 'n_estimators': 20}
ab = AdaBoostClassifier(**ab_params)
ab.fit(X_train,y_train)
ab_pred = ab.predict(test_data)
Prediction['AB'] = ab_pred

### SVC

[[back to top](#Table-of-contents)]

In [ ]:
# Pipeline setup
models = { 
    'SVC': SVC()
}

# Parameters setup
params = {
    'SVC': [
        {'kernel': ['poly'], 'C': [0.3,0.4,0.5,0.6,0.7,0.8,0.9,1], 
                            'gamma': [0.08,0.09,0.1,0.11,0.12],
                            'degree': [2,3]}]}

# Lancer la grid search
df_best_svc , dic_best_svc, d_res_svc = grid_search_global('clas',models,params,class_names=columns_name)

In [ ]:
# Results dataframe
d_res_svc

In [ ]:
# Selection of the parameters to study
index_selection = [14,32,41,50]
svc_study = d_res_svc.loc[index_selection,['Algo','params','mean_test_score','mean_train_score']]
svc_study

In [ ]:
# Learning curve
df_study = svc_study
index = list(df_study.index)
for ind in index :
    algo = df_study.loc[ind, 'Algo']
    params = df_study.loc[ind, 'params']
    mean_test = df_study.loc[ind, 'mean_test_score']
    mean_train = df_study.loc[ind, 'mean_train_score']
    title = "Learning Curves for the estimator %s which results are \n mean test:%s \n mean train %s \n with parameters %s)" % (algo,mean_test,mean_train,params)
    cv = ShuffleSplit(n_splits=50, test_size=0.2, random_state=0)
    estimator = models[algo]
    estimator.set_params(**params)
    plot_learning_curve(estimator, title, data, target, (0.3, 1.01), cv=cv, n_jobs=-1)
    plt.show()

In [ ]:
# Validation parameters setup
dict_Validation = { 
    'SVC': { 'C': np.linspace(0.01,1,20),
              'gamma': np.linspace(0.01,0.4,20),
              'degree': [2,3]}  
    }

for ind in index :
    algo = df_study.loc[ind, 'Algo']
    params = df_study.loc[ind, 'params']
    mean_test = df_study.loc[ind, 'mean_test_score']
    mean_train = df_study.loc[ind, 'mean_train_score']
    print("Model: %s\nMean test: %s\nMean train: %s\nParams: %s" % (algo,mean_test,mean_train,params))
    estimator = models[algo]
    estimator.set_params(**params)
    cv = ShuffleSplit(n_splits=10, test_size=0.2, random_state=0)
    for key, value in dict_Validation[algo].items():
        plot_validation_curve(estimator, algo, key, value, X_train, y_train, scoring='accuracy', cv=cv)
        plt.show()

In [ ]:
# Prediction
svc_params = {'C': 0.8, 'degree': 2, 'gamma': 0.08, 'kernel': 'poly'}
svc = SVC(**svc_params)
svc.fit(data,target)
svc_pred = svc.predict(test_data)
Prediction['SVC'] = svc_pred

### Logistic Regression

[[back to top](#Table-of-contents)]

In [ ]:
from sklearn.linear_model import LogisticRegression
# Pipeline setup
models = { 
    'LogisticRegression': LogisticRegression()
}

# Parameters setup
params = {'LogisticRegression' : { 'C': [0.1,0.2,0.3,0.4,0.5,0.6,0.8,0.9,1],
           'penalty': ['l2'],
           'solver': ['newton-cg','lbfgs','liblinear','sag'],
           'max_iter': [100,250,500],
           'tol':  [1e-4,3e-4,7e-4,1e-3,3e-3],
          }
         }

# Lancer la grid search
df_best_svc , dic_best_svc, d_res_svc = grid_search_global('clas',models,params,class_names=columns_name)

In [ ]:
# Results dataframe
d_res

In [ ]:
# Selection of the parameters to study
index_selection = [177,130,106,63,87,86]
df_study = d_res.loc[index_selection,['Algo','params','mean_test_score','mean_train_score']]
df_study

In [ ]:
# Learning curve
index = list(df_study.index)
for ind in index :
    algo = df_study.loc[ind, 'Algo']
    params = df_study.loc[ind, 'params']
    mean_test = df_study.loc[ind, 'mean_test_score']
    mean_train = df_study.loc[ind, 'mean_train_score']
    title = "Learning Curves for the estimator %s which results are \n mean test:%s \n mean train %s \n with parameters %s)" % (algo,mean_test,mean_train,params)
    cv = ShuffleSplit(n_splits=50, test_size=0.2, random_state=0)
    estimator = models[algo]
    estimator.set_params(**params)
    plot_learning_curve(estimator, title, data, target, (0.3, 1.01), cv=cv, n_jobs=-1)
    plt.show()

In [ ]:
# Validation parameters setup
dict_Validation = { 
    'GradientBoostingClassifier': {'n_estimators': range(1,50,2),
                                  'learning_rate': np.linspace(0.01,0.5,50),
                                  'max_depth': range(1,5,1)}  
}

for ind in index :
    algo = df_study.loc[ind, 'Algo']
    params = df_study.loc[ind, 'params']
    mean_test = df_study.loc[ind, 'mean_test_score']
    mean_train = df_study.loc[ind, 'mean_train_score']
    print("Model: %s\nMean test: %s\nMean train: %s\nParams: %s" % (algo,mean_test,mean_train,params))
    estimator = models[algo]
    estimator.set_params(**params)
    cv = ShuffleSplit(n_splits=10, test_size=0.2, random_state=0)
    for key, value in dict_Validation[algo].items():
        plot_validation_curve(estimator, clef, key, value, X_train, y_train, scoring='accuracy', cv=cv)
        plt.show()

In [ ]:
# Prediction 
lr_parm = {'C': 1, 'max_iter': 100, 'penalty': 'l2', 'solver': 'newton-cg', 'tol': 0.0001}
lr = LogisticRegression(**lr_parm)
lr.fit(X_train,y_train)
lr_pred = lr.predict(test_data)
Prediction['LR'] = lr_pred

### Voting Classifier

[[back to top](#Table-of-contents)]

In [ ]:
# Train & Test
X_train, X_test, y_train, y_test = train_test_split(data, target, test_size=0.20,random_state =123)

In [ ]:
# Classifier default parameters
abc = AdaBoostClassifier(learning_rate = 0.5, n_estimators = 20)        
lda = LinearDiscriminantAnalysis(n_components = 2, solver='svd')
lr = LogisticRegression()
svc = SVC(probability=True)
rfc = RandomForestClassifier()
gbc = GradientBoostingClassifier()

ab_params = {'learning_rate': 0.3, 'n_estimators': 30}
GBC_params = {'learning_rate': 0.1, 'loss': 'exponential', 'max_depth': 3, 'max_features': 10, 'min_samples_leaf': 7, 'min_samples_split': 5, 'n_estimators': 10}
RF_params =  {'criterion': 'entropy', 'max_features': 4, 'min_samples_leaf': 8, 'min_samples_split': 9, 'n_estimators': 11}

# Classifier Tunep parameters
abc_tp = AdaBoostClassifier(**ab_params)  
lda_tp = LinearDiscriminantAnalysis(n_components = 2, solver='svd')
lr_tp = LogisticRegression(C = 0.2, max_iter = 10, n_jobs = -1, penalty = 'l2', solver = 'sag', tol = 0.001)
svc_tp = SVC(C=0.5, gamma=0.10, kernel='poly', degree=3, probability= True)
rfc_tp = RandomForestClassifier(**RF_params)
gbc_tp = GradientBoostingClassifier(**GBC_params)

models = { 
    'VotingClassifier': VotingClassifier(estimators= [('abc_tp', abc_tp),('rfc_tp', rfc_tp), ('gbc_tp', gbc_tp)])
}

# Parameters setup
params = {'VotingClassifier' : {'voting': ['soft','hard']}
         }

# Lancer la grid search
df_best_vc , dic_best_vc, d_res_vc = grid_search_global('clas',models,params,class_names=columns_name)

In [ ]:
# Classifier Tunep parameters
# Score 0.77

GBC_params = {'learning_rate': 0.2, 'loss': 'deviance', 'max_depth': 3, 'max_features': 10, 'min_samples_leaf': 7, 'min_samples_split': 6, 'n_estimators': 10}
RF_params =  {'criterion': 'entropy', 'max_features': 10, 'min_samples_leaf': 10, 'min_samples_split': 3, 'n_estimators': 30}

rfc_tp = RandomForestClassifier(**RF_params)
gbc_tp = GradientBoostingClassifier(**GBC_params)

# [ ('lr_tp', lr_tp),('lda_tp', lda_tp), ('svc_tp', svc_tp), ('rfc_tp', rfc_tp), ('gbc_tp', gbc_tp)]
VC_tp_soft = VotingClassifier(estimators=[('rfc_tp', rfc_tp), ('gbc_tp', gbc_tp)],   
                                         voting='soft')
VC_tp_soft.fit(X_train,y_train)
Prediction['VC_tp_soft'] = VC_tp_soft.predict(Eval_OH_Std)

In [ ]:
# Classifier Not Tunep parameters
# Score 0.77

abc = AdaBoostClassifier(learning_rate = 0.5, n_estimators = 20)        
lda = LinearDiscriminantAnalysis(n_components = 2, solver='svd')
lr = LogisticRegression()
svc = SVC(probability=True)
rfc = RandomForestClassifier()
gbc = GradientBoostingClassifier()



VC_nottp_soft = VotingClassifier(estimators=[ ('lr_tp', lr_tp),('lda_tp', lda_tp), ('svc_tp', svc_tp), ('rfc_tp', rfc_tp), ('gbc_tp', gbc_tp)],
                                         voting='soft')
VC_nottp_soft.fit(data,target)
Prediction['VC_nottp_soft'] = VC_nottp_soft.predict(Eval_OH_Std)

In [ ]:
pd.set_option('display.max_colwidth', -1)

In [ ]:
Eval_OH_Std.shape

In [ ]:
Prediction.shape

#### Save best params

In [ ]:
# 0.79-0.81 with PassId_0.81 and without ticket and cabin and dropping 'Title_aggr_Royalty','Title_aggr_Officer','Name_Size_Medium','Embarked_Q'
GBC_params = {'learning_rate': 0.2, 'loss': 'deviance', 'max_depth': 3, 'max_features': 10, 'min_samples_leaf': 7, 'min_samples_split': 6, 'n_estimators': 10}
# 0.80 same conditions
RF_params =  {'criterion': 'entropy', 'max_features': 10, 'min_samples_leaf': 10, 'min_samples_split': 3, 'n_estimators': 30}
#0.79
VotingClassifier(estimators=[('rfc_tp', rfc_tp), ('gbc_tp', gbc_tp)],voting='soft')

#### Save X_train and y_train that generalize well

In [ ]:
Pass_Id = list(X_train.index)
Pass_Id

In [ ]:
PasId = pd.DataFrame({
        "PassengerId": Pass_Id
    })
PasId.to_csv('PassId_0.81.csv', index=False)

#### Save Number of random state that are good

### Submission

[[back to top](#Table-of-contents)]

In [ ]:
estim = #  Remplir ici
Prediction = estim.predict(Eval_OH_Std)

In [ ]:
Predic = Prediction['GBC']

In [ ]:
submission = pd.DataFrame({
        "PassengerId": PassengerId,
        "Survived": Predic
    })
submission.to_csv('titanic_all_data_R999_GBC2_pred.csv', index=False)